In [3]:
import pandas as pd
url = f'{"https://github.com/DataTalksClub/llm-zoomcamp/blob/main/04-monitoring/data/results-gpt4o-mini.csv"}?raw=1'
df = pd.read_csv(url)
df = df.iloc[:300]

In [6]:
# Load the embedding model
from sentence_transformers import SentenceTransformer
embedding_model = SentenceTransformer('multi-qa-mpnet-base-dot-v1')

# Extract the first LLM answer
answer_llm = df.iloc[0].answer_llm

# Generate embeddings
embedding = embedding_model.encode(answer_llm)

/usr/local/python/3.10.13/lib/python3.10/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/212 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/8.71k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

/usr/local/python/3.10.13/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [7]:
embedding

array([-4.22446549e-01, -2.24856257e-01, -3.24058414e-01, -2.84758478e-01,
        7.25642918e-03,  1.01186566e-01,  1.03716910e-01, -1.89983174e-01,
       -2.80599259e-02,  2.71588802e-01, -1.15337655e-01,  1.14666030e-01,
       -8.49586725e-02,  3.32365334e-01,  5.52720726e-02, -2.22195774e-01,
       -1.42540857e-01,  1.02519155e-01, -1.52333647e-01, -2.02912465e-01,
        1.98422875e-02,  8.38149190e-02, -5.68632066e-01,  2.32844148e-02,
       -1.67292684e-01, -2.39256918e-01, -8.05464387e-02,  2.57084146e-02,
       -8.15464780e-02, -7.39290118e-02, -2.61550009e-01,  1.92575473e-02,
        3.22909206e-01,  1.90357104e-01, -9.34726413e-05, -2.13165611e-01,
        2.88943425e-02, -1.79530401e-02, -5.92756271e-02,  1.99918285e-01,
       -4.75170948e-02,  1.71634093e-01, -2.45917086e-02, -9.38061550e-02,
       -3.57002735e-01,  1.33263692e-01,  1.94045901e-01, -1.18530318e-01,
        4.56915230e-01,  1.47728190e-01,  3.35945129e-01, -1.86959356e-01,
        2.45954901e-01, -

In [12]:

# Function to compute similarity between original and LLM-generated answers
def compute_similarity(record):
    answer_orig = record['answer_orig']
    answer_llm = record['answer_llm']
    
    # Generate embeddings for both original and LLM answers
    v_orig = embedding_model.encode(answer_orig)
    v_llm = embedding_model.encode(answer_llm)
    
    # Compute the dot product between the two embeddings
    return np.dot(v_orig, v_llm)

# Compute similarities for all records
similarity_scores = []

# Iterate over each record in the dataframe and compute similarity
for _, record in tqdm(df.iterrows(), total=len(df)):
    similarity = compute_similarity(record)
    similarity_scores.append(similarity)

df['cosine'] = similarity_scores


percentile_75 = np.percentile(similarity_scores, 75)



  0%|          | 0/300 [00:00<?, ?it/s]

In [13]:
percentile_75

np.float32(31.674309)

In [14]:

def normalize_vector(v):
    norm = np.sqrt(np.sum(v * v))
    return v / norm


def compute_cosine_similarity(record):
    answer_orig = record['answer_orig']
    answer_llm = record['answer_llm']
    
   
    v_orig = embedding_model.encode(answer_orig)
    v_llm = embedding_model.encode(answer_llm)
    
    # Normalize both vectors
    v_orig_norm = normalize_vector(v_orig)
    v_llm_norm = normalize_vector(v_llm)
    

    cosine_similarity = np.dot(v_orig_norm, v_llm_norm)
    
    return cosine_similarity


cosine_scores = []


for _, record in tqdm(df.iterrows(), total=len(df)):
    cosine_similarity = compute_cosine_similarity(record)
    cosine_scores.append(cosine_similarity)


df['cosine'] = cosine_scores


percentile_75 = np.percentile(cosine_scores, 75)

  0%|          | 0/300 [00:00<?, ?it/s]

In [15]:
percentile_75

np.float32(0.8362349)

In [16]:
# pip install rouge

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)



[notice] A new release of pip is available: 24.1.2 -> 24.2
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [17]:
from rouge import Rouge

In [19]:
# Select the specific record at index 10
r = df.iloc[10]

In [20]:

rouge_scorer = Rouge()
scores = rouge_scorer.get_scores(r['answer_llm'], r['answer_orig'])[0]

rouge_1_f1 = scores['rouge-1']['f']

In [21]:
rouge_1_f1

0.45454544954545456

In [23]:

rouge_1_f1 = scores['rouge-1']['f']
rouge_2_f1 = scores['rouge-2']['f']
rouge_l_f1 = scores['rouge-l']['f']

# Compute the average F1 score
average_f1 = (rouge_1_f1 + rouge_2_f1 + rouge_l_f1) / 3


In [24]:
average_f1

0.35490034990035496

In [25]:

rouge_1_f1_scores = []
rouge_2_f1_scores = []
rouge_l_f1_scores = []


for _, row in tqdm(df.iterrows(), total=len(df)):
    scores = rouge_scorer.get_scores(row['answer_llm'], row['answer_orig'])[0]
    
    
    rouge_1_f1_scores.append(scores['rouge-1']['f'])
    rouge_2_f1_scores.append(scores['rouge-2']['f'])
    rouge_l_f1_scores.append(scores['rouge-l']['f'])


f1_scores_df = pd.DataFrame({
    'rouge_1_f1': rouge_1_f1_scores,
    'rouge_2_f1': rouge_2_f1_scores,
    'rouge_l_f1': rouge_l_f1_scores
})


average_rouge_2_f1 = f1_scores_df['rouge_2_f1'].mean()

  0%|          | 0/300 [00:00<?, ?it/s]

In [26]:
average_rouge_2_f1

np.float64(0.20696501983423318)